In [1]:
# !pip install -q accelerate peft bitsandbytes transformers trl faiss-gpu langchain_community wandb flash-attn
!pip install -q accelerate peft bitsandbytes transformers trl datasets

# flash-attn

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 69.1/69.1 MB 11.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 293.4/293.4 kB 23.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 37.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 8.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 11.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 13.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 17.7 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.9.0 which is incompatible.


In [2]:
# load the required packages.
import torch
from datasets import load_dataset, Dataset
from peft import LoraConfig, AutoPeftModelForCausalLM, PeftModel, get_peft_model
from transformers import AutoModelForCausalLM, AutoTokenizer, BitsAndBytesConfig, TrainingArguments, AutoConfig, set_seed
from trl import SFTTrainer
import bitsandbytes as bnb
import transformers

import os
import numpy as np
import pandas as pd
import sqlparse
import re
import json

from huggingface_hub import hf_hub_download
from huggingface_hub import HfFileSystem

In [ ]:
#transformers.logging.set_verbosity_info()

In [3]:
WRITE_TOKEN = userdata.get('hf_write')
READ_TOKEN = userdata.get('hf_read')

In [4]:
model_name = "stabilityai/stable-code-instruct-3b"
out_name = "lleticiasilvaa/StableCode-text2SQL-withoutquantization"
prev_checkpoint = None

In [ ]:
#!huggingface-cli login

In [5]:
spider_id="NESPED-GEN/spider_selector_schemaReduzido"

### Load Data


In [6]:
spider = load_dataset(spider_id, split="train")
spider

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/1.02k [00:00<?, ?B/s]

dev-00000-of-00001.parquet:   0%|          | 0.00/429k [00:00<?, ?B/s]

train-00000-of-00001.parquet:   0%|          | 0.00/3.07M [00:00<?, ?B/s]

Generating dev split:   0%|          | 0/1034 [00:00<?, ? examples/s]

Generating train split:   0%|          | 0/8656 [00:00<?, ? examples/s]

Dataset({
    features: ['db_id', 'question_en', 'query', 'answer', 'hardness', 'query_llm', 'schema_SQLDatabase', 'schema_SQLDatabase_min', 'schema_our', 'schema_our_min', 'schema_dict', 'selector', 'selector_correct', 'schema_SQLDatabase_reduzido', 'schema_SQLDatabase_reduzido_tabelas', 'selector_parser'],
    num_rows: 8656
})

In [7]:
df = spider.to_pandas()

# Load Base Model

In [8]:
def download_checkpoint(adapter_model_id, checkpoint):
    fs = HfFileSystem()
    for file in fs.ls(f'{adapter_model_id}/{checkpoint}', detail=False):
        file_name = file.split(checkpoint)[-1]

        hf_hub_download(repo_id=adapter_model_id, filename=(f'{checkpoint}{file_name}'), local_dir='out')

    for file in fs.ls(f'{adapter_model_id}/logs', detail=False):
        file_name = file.split(checkpoint)[-1]

        hf_hub_download(repo_id=adapter_model_id, filename=(f'logs/{file_name.split("/")[-1]}'), local_dir='out')

In [ ]:
# download_checkpoint(out_name, prev_checkpoint)

In [9]:
seed=14


if (prev_checkpoint != None):
    try:
        download_checkpoint(out_name, prev_checkpoint)
    except:
        pass
tokenizer = AutoTokenizer.from_pretrained(model_name, trust_remote_code=True, token=READ_TOKEN, map_device="auto", add_eos_token=True, use_fast=True)

new_tokens = {'additional_special_tokens': ['[SQL]','[/SQL]', '[QUESTION]','[/QUESTION]']}
#adicionar tokens especiais:
# if (prev_checkpoint == None):
#     tokenizer.add_special_tokens(new_tokens)


if torch.cuda.is_bf16_supported():
  compute_dtype = torch.bfloat16
  attn_implementation = 'flash_attention_2'
else:
  compute_dtype = torch.float16
  attn_implementation = 'sdpa'

tokenizer.pad_token = tokenizer.eos_token
tokenizer.padding_side = "right"


bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=compute_dtype,
    bnb_4bit_use_double_quant=False,
)

model = AutoModelForCausalLM.from_pretrained(
    model_name,
    torch_dtype=compute_dtype,
    device_map="auto",
    # quantization_config=bnb_config,

    trust_remote_code=True,
    token=READ_TOKEN,
    # attn_implementation=attn_implementation
)

# se adicionar special_tokens tem que fazer resize do tokenizer:
# model.resize_token_embeddings(len(tokenizer))

## model.resize_token_embeddings(max(len(tokenizer), model.config.vocab_size))

tokenizer_config.json:   0%|          | 0.00/9.35k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.12M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/587 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/738 [00:00<?, ?B/s]

model.safetensors.index.json:   0%|          | 0.00/29.4k [00:00<?, ?B/s]

model-00001-of-00002.safetensors:   0%|          | 0.00/4.98G [00:00<?, ?B/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/610M [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/132 [00:00<?, ?B/s]

In [10]:
model

StableLmForCausalLM(
  (model): StableLmModel(
    (embed_tokens): Embedding(50304, 2560)
    (layers): ModuleList(
      (0-31): 32 x StableLmDecoderLayer(
        (self_attn): StableLmSdpaAttention(
          (q_proj): Linear(in_features=2560, out_features=2560, bias=False)
          (k_proj): Linear(in_features=2560, out_features=2560, bias=False)
          (v_proj): Linear(in_features=2560, out_features=2560, bias=False)
          (o_proj): Linear(in_features=2560, out_features=2560, bias=False)
          (attention_dropout): Dropout(p=0.0, inplace=False)
          (rotary_emb): StableLmRotaryEmbedding()
        )
        (mlp): StableLmMLP(
          (gate_proj): Linear(in_features=2560, out_features=6912, bias=False)
          (up_proj): Linear(in_features=2560, out_features=6912, bias=False)
          (down_proj): Linear(in_features=6912, out_features=2560, bias=False)
          (act_fn): SiLU()
        )
        (input_layernorm): LayerNorm((2560,), eps=1e-05, elementwise_affin

In [ ]:
# se adicionar special_tokens tem que fazer resize do tokenizer:
#model.resize_token_embeddings(len(tokenizer))

#model.resize_token_embeddings(max(len(tokenizer), model.config.vocab_size))

The new embeddings will be initialized from a multivariate normal distribution that has old embeddings' mean and covariance. As described in this article: https://nlp.stanford.edu/~johnhew/vocab-expansion.html. To disable this, use `mean_resizing=False`
The new lm_head weights will be initialized from a multivariate normal distribution that has old embeddings' mean and covariance. As described in this article: https://nlp.stanford.edu/~johnhew/vocab-expansion.html. To disable this, use `mean_resizing=False`


Embedding(32004, 2048)

#### Chat Template - Gerar SQL

In [ ]:
# tokenizer.chat_template = """
# {% if messages[0]['role'] == 'system' %}
#     {% set loop_messages = messages[1:] %}
#     {% set system_message = messages[0]['content'] %}
# {% else %}
#     {% set loop_messages = messages %}
#     {% set system_message = 'Given a user question and the schema of a database, your task is to generate an SQL query that accurately answers the question based on the provided schema.' %}
# {% endif %}
# {{ '# <|system|>/n/' + system_message + '/n//n/' }}
# {% if messages|selectattr("role", "equalto", "example")|list %}
#     Below are some examples of question and their corresponding SQL queries:/n//n/
# {% else %}
#     /n/
# {% endif %}
# {% for message in loop_messages %}
#     {% if message['role'] == 'example' %}
#         {{ message['content'] }}/n//n/
#     {% elif message['role'] == 'schema' %}
#         # <|schema|>/n/The query will run on a database with the following schema:/n/{{ message['content'] }}/n//n/
#     {% elif message['role'] == 'user' %}
#         # <|user|>/n/[QUESTION]{{ message['content'] }}[/QUESTION]/n//n/
#     {% elif message['role'] == 'assistant' %}
#         # <|assistant|>/n/[SQL]{{ message['content'] }}[/SQL]
#     {% endif %}
# {% endfor %}
# {% if add_generation_prompt %}
#     # <|assistant|>/n/[SQL]
# {% endif %}
# """.replace("\n","").replace("  ", "").replace("/n/", "\n")

In [11]:
import re

def replace_alias_with_table(query):
    # Expressão regular para encontrar tabelas com alias, capturando o nome da tabela e o alias
    alias_pattern = re.compile(r'(\bFROM\b|\bJOIN\b)\s+(\w+)\s+AS\s+(\w+)', re.IGNORECASE)

    # Substituições de aliases encontrados no padrão
    aliases = {match.group(3): match.group(2) for match in alias_pattern.finditer(query)}

    # Substituir cada alias pelo nome da tabela correspondente
    for alias, table in aliases.items():
        query = re.sub(r'\b' + alias + r'\b', table, query)

    # Remover 'AS' e alias das cláusulas 'FROM' e 'JOIN'
    query = re.sub(r'\bAS\s+\w+', '', query, flags=re.IGNORECASE)
    return query

In [12]:
def to_sql(query):
  return sqlparse.format(replace_alias_with_table(query), reindent=True, keyword_case='upper')

def apply_template(row, tokenizer=tokenizer, n_examplea=0):
    question = row['question_en']
    schema = row['schema_SQLDatabase']
    sql = to_sql(row['query'])

    system = "Given a user question and the schema of a database, your task is to generate an SQL query that accurately answers the question based on the provided schema."

    chat = [
            {'role': 'system', 'content': system},
            {'role': 'user', 'content': f"# Schema:\n```sql\n{schema}\n```\n\n# Question: {question}"},
            {'role': 'assistant', 'content': f"```sql\n{sql}\n```\n"}
            ]

    row['text'] = tokenizer.apply_chat_template(chat, tokenize=False, add_generation_prompt=False)

    return row

In [13]:
df = df.apply(apply_template, axis=1)

In [ ]:
df.head()

In [ ]:
# df['n_tokens'] = df['text'].apply(lambda x: len(tokenizer.encode(x)))

In [ ]:
# import seaborn as sns
# sns.histplot(df['n_tokens'])

In [14]:
print(df['text'][df.index[50]])

<|im_start|>system
Given a user question and the schema of a database, your task is to generate an SQL query that accurately answers the question based on the provided schema.<|im_end|>
<|im_start|>user
# Schema:
```sql
CREATE TABLE city (
        City_ID INT,
        Official_Name TEXT,
        Status TEXT,
        Area_km_2 REAL,
        Population REAL,
        Census_Ranking TEXT,
        PRIMARY KEY (City_ID)
);

CREATE TABLE farm (
        Farm_ID INT,
        Year INT,
        Total_Horses REAL,
        Working_Horses REAL,
        Total_Cattle REAL,
        Oxen REAL,
        Bulls REAL,
        Cows REAL,
        Pigs REAL,
        Sheep_and_Goats REAL,
        PRIMARY KEY (Farm_ID)
);

CREATE TABLE farm_competition (
        Competition_ID INT,
        Year INT,
        Theme TEXT,
        Host_city_ID INT,
        Hosts TEXT,
        PRIMARY KEY (Competition_ID),
        FOREIGN KEY (Host_city_ID) REFERENCES city(City_ID)
);

CREATE TABLE competition_record (
        Competi

In [15]:
_df = pd.DataFrame(columns=['text'])
_df['text'] = df.sample(frac=1, random_state=14).reset_index(drop=True)['text']
_df = Dataset.from_pandas(_df)
_df = _df.train_test_split(test_size=0.01, shuffle=True, seed=14)
train_dataset, valid_dataset = _df["train"], _df["test"]

#### Chat Template - Schema Linking

In [ ]:
def apply_template(row, tokenizer=tokenizer, n_examplea=0):
    question = row['question_en']
    schema = row['schema_dict']
    schema_linking = row['selector_correct']

    system = "Given a user question and the schema of a database, your task is to generate an JSON with the the names of tables and columns of the schema that the question is referring to."

    chat = [
          {'role': 'system', 'content': system},
          {'role': 'user', 'content': f"# Schema:\n```sql\n{schema}\n```\n\n# Question: {question}"},
          {'role': 'assistant', 'content': f"```json\n{schema_linking}\n```"}
          ]

    row['text'] = tokenizer.apply_chat_template(chat, tokenize=False, add_generation_prompt=False)

    return row

In [ ]:
df = df.apply(apply_template, axis=1)

In [ ]:
# df['n_tokens'] = df['text'].apply(lambda x: len(tokenizer.encode(x)))
# import seaborn as sns
# sns.histplot(df['n_tokens'])

In [ ]:
print(df['text'][df.index[70]])

<|im_start|>system
Given a user question and the schema of a database, your task is to generate an JSON with the the names of tables and columns of the schema that the question is referring to.<|im_end|>
<|im_start|>user
# Schema:
```sql
{
  'Addresses': ['address_id', 'line_1', 'line_2', 'city', 'zip_postcode', 'state_province_county', 'country'],
  'People': ['person_id', 'first_name', 'middle_name', 'last_name', 'cell_mobile_number', 'email_address', 'login_name', 'password'],
  'Students': ['student_id', 'student_details'],
  'Courses': ['course_id', 'course_name', 'course_description', 'other_details'],
  'People_Addresses': ['person_address_id', 'person_id', 'address_id', 'date_from', 'date_to'],
  'Student_Course_Registrations': ['student_id', 'course_id', 'registration_date'],
  'Student_Course_Attendance': ['student_id', 'course_id', 'date_of_attendance'],
  'Candidates': ['candidate_id', 'candidate_details'],
  'Candidate_Assessments': ['candidate_id', 'qualification', 'asses

In [ ]:
_df = pd.DataFrame(columns=['text'])
_df['text'] = df.sample(frac=1, random_state=14).reset_index(drop=True)['text']
_df = Dataset.from_pandas(_df)
_df = _df.train_test_split(test_size=0.01, shuffle=True, seed=14)
train_dataset, valid_dataset = _df["train"], _df["test"]

### Finetuning

In [16]:
from huggingface_hub import login, create_repo
from google.colab import userdata
import wandb
import os

#token = userdata.get('hf_write')
token = WRITE_TOKEN
login(token=token)
set_seed(1234)

In [ ]:
def find_all_linear_names(model, new_tokens=False):
    lora_module_names = set()
    for name, module in model.named_modules():
        if isinstance(module, bnb.nn.Linear4bit) or isinstance(module, bnb.nn.Linear8bitLt):
            names = name.split(".")
            lora_module_names.add(names[0] if len(names) == 1 else names[-1])
    if(new_tokens):
      lora_module_names.add("lm_head")
    return list(lora_module_names)

In [ ]:
# modules = find_all_linear_names(model)
# print(f"Found {len(modules)} modules to quantize: {modules}")

Found 0 modules to quantize: []


In [17]:
peft_config = LoraConfig(
    lora_alpha=128, #primeira versão = 16
    lora_dropout=0.1,
    r=64,
    # bias="none",
    # task_type="CAUSAL_LM",
    #target_modules=modules,
    # modules_to_save=["embed_tokens"], #quando adicionar tokens speciais
)

In [18]:
torch.cuda.empty_cache()

In [21]:
from trl.trainer.sft_config import SFTConfig

steps=100
strategy="steps"

trainer = SFTTrainer(
    model= model,
    processing_class=tokenizer,

    train_dataset=train_dataset,
    eval_dataset=valid_dataset,

    peft_config=peft_config,

    args= SFTConfig(
      output_dir="out",

      dataset_text_field="text",
      max_seq_length = 2048,

      save_strategy=strategy,
      save_steps= steps,

      logging_strategy=strategy,
      logging_steps=steps,
      logging_dir="out/logs",

      eval_strategy=strategy,
      eval_steps=steps,

      num_train_epochs=1,
      per_device_train_batch_size=1,
      per_device_eval_batch_size=1,
      gradient_accumulation_steps=8, #primeira versão era 1
      gradient_checkpointing=True,
      fp16=True,
      bf16=False,

      optim="paged_adamw_8bit",
      learning_rate=1e-4, #primeira versão era 2e-4,
      weight_decay=0.001,
      max_grad_norm=0.3,
      max_steps=-1,
      warmup_ratio=0.03,
      group_by_length=True,
      lr_scheduler_type="cosine", #primeira versão era linear
      seed= seed,


      report_to=["tensorboard"],
      push_to_hub=True,
      hub_strategy="all_checkpoints",
      hub_model_id=out_name,

      label_names=["labels"]
  )

)
if(prev_checkpoint != None):
    trainer.train(f"out/{prev_checkpoint}")
else:
    trainer.train()

Map:   0%|          | 0/8569 [00:00<?, ? examples/s]

Map:   0%|          | 0/87 [00:00<?, ? examples/s]

Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Tr

Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.
Trainer.tokenizer is now deprecated. You should use Trainer.processing_class instead.


In [22]:
trainer.push_to_hub()

CommitInfo(commit_url='https://huggingface.co/lleticiasilvaa/StableCode-text2SQL-withoutquantization/commit/824d58e45c7106e0a6f1adc911c85662e2f7f3df', commit_message='End of training', commit_description='', oid='824d58e45c7106e0a6f1adc911c85662e2f7f3df', pr_url=None, repo_url=RepoUrl('https://huggingface.co/lleticiasilvaa/StableCode-text2SQL-withoutquantization', endpoint='https://huggingface.co', repo_type='model', repo_id='lleticiasilvaa/StableCode-text2SQL-withoutquantization'), pr_revision=None, pr_num=None)